In [1]:
import pandas as pd
import numpy as np 
import glob
import os 

In [2]:
# O QUE PRECISA PRA RODAR ESSE CÓDIGO:

# Arquivo Draft
# Arquivo Estoque
# Arquivo BI preço
# Arquivo pdv
# Arquivo Calendario
# Arquivo tabela de compra

#Atualizar o nome da marca no filtro do estoque.

In [3]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202510\DRAFT_PDVS_SEM"   # arquivo dos drafts

# Pattern to match all CSV files
csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)


df_draft.shape


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_42880\119945099.py:10: DtypeWarning: Columns (7) have mixed types. Specify dtype option on import or set low_memory=False.
  df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)


(115164, 46)

In [4]:
df_draft['match'] = 1 


In [5]:


# Caminho onde estão as subpastas com os arquivos CSV
pasta_entrada =  r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202510\estoque"

# Lista todas as subpastas dentro de "ESTOQUE"
subpastas = [os.path.join(pasta_entrada, d) for d in os.listdir(pasta_entrada) if os.path.isdir(os.path.join(pasta_entrada, d))]

df_list = []

# Percorre todas as subpastas
for subpasta in subpastas:
    arquivos = [f for f in os.listdir(subpasta) if f.endswith(".csv")]
    nome_pasta = os.path.basename(subpasta)  # Obtém o nome da pasta

    for arquivo in arquivos:
        caminho_arquivo = os.path.join(subpasta, arquivo)
        try:
            df = pd.read_csv(caminho_arquivo, encoding="utf-8", low_memory=False)  # Melhor para grandes volumes de dados
            df["Arquivo_Origem"] = arquivo  # Adiciona o nome do arquivo de origem
            df["Pasta_Origem"] = nome_pasta  # Adiciona o nome da pasta de origem
            df_list.append(df)
        except Exception as e:
            print(f"Erro ao ler o arquivo {arquivo}: {e}")

if df_list:
    df_estoque = pd.concat(df_list, ignore_index=True)

df_estoque['PDV'] = df_estoque['PDV'].astype(str)

df_estoque['SKU_FINAL'] = np.where(df_estoque['SKU_PARA'] == "-", df_estoque['SKU'], df_estoque['SKU_PARA'])

df_estoque['SKU_FINAL']=df_estoque['SKU_FINAL'].astype(str)


In [6]:
df_bi_preco = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202510\preçobi\TABELA DE PREÇOS (4).xlsx")

c:\Users\joao.herculano\AppData\Local\Programs\Python\Python313\Lib\site-packages\openpyxl\styles\stylesheet.py:237: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")


In [7]:
df_bi_preco.columns

Index(['SKU1', 'SKU2', 'Descrição', 'MARCA', 'CATEGORIA', 'LINHA', 'UF',
       'Tipo Preço', 'PC', 'PV'],
      dtype='object')

In [8]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202509\arquivos pra gerar\pdvs\PDV_ATT.xlsx")
df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})
df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO', 'SUPERVISOR', 'STATUS'])
df_pdv['PDV'] = df_pdv['PDV DESC'].str.split("-").str[0].str.strip()


In [9]:
#ignorando a PDV que ainda não está online
df_pdv = df_pdv[df_pdv['DESCRIÇÃO PDV'] != '23813-COMERCIO-HIB VALENTE']

In [10]:
df_pdv['MATCH'] = 1

**ALTERAR NOME DA COLUNA "ARQUIVO_ORIGEM" PARA UMA DAS OPÇÕES ABAIXO:**

*BOT.csv* 

*EUD.csv*

*QDB.csv*

In [11]:
df_estoque = df_estoque[df_estoque['Arquivo_Origem']== "EUD.csv"]

In [12]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")

In [13]:
calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)
calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]


calendario = calendario[calendario['MARCA'] == "EUDORA"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2)

ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]


# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]


filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)



In [14]:
filtered_calendario

Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO   MARCA       Date  NUM_CICLO  \
2262  C202511   2025-07-16 2025-08-05       21  EUDORA 2025-07-16         11   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  
2262     C2025    C202513               42

In [15]:
filtered_calendario['match'] = 1

In [16]:
df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

In [17]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\EUDORA\202510\tabela promo\Tabela-de-Promocoes_C10_att-1747056411627.xlsx.xlsx")


In [18]:
df_tabela = df_tabela[[    'Ciclo',                 'Veiculo',
              'Tipo de Promoção',  'Estratégia de Promoção',
                 'Tipo_mecanica', 'Promo Período Limitado?',
                           'EAM',               'Categoria',
                    'Cód. Combo',          'Código do Item',
             'Descrição do Item',     'Chamada Promocional',
                 'Valor do Guia',      'Preço Promocionado',
                 '% de Desconto',           'RE compra por',
                  'RE Vende por',          'RE lucra  (R$)']]

In [19]:
df_tabela['Código do Item'] = df_tabela['Código do Item'].astype(str).str.replace(".0","",regex=False)

In [20]:
df_tabela['MATCH'] = 1

In [21]:
df_tabela = pd.merge(left=df_tabela,right=df_pdv[['PDV','MATCH','UF','DESCRIÇÃO PDV','ANALISTA']],on='MATCH',how='inner')

In [22]:
df_tabela = df_tabela.drop_duplicates()

In [23]:
df_tabela.columns

Index(['Ciclo', 'Veiculo', 'Tipo de Promoção', 'Estratégia de Promoção',
       'Tipo_mecanica', 'Promo Período Limitado?', 'EAM', 'Categoria',
       'Cód. Combo', 'Código do Item', 'Descrição do Item',
       'Chamada Promocional', 'Valor do Guia', 'Preço Promocionado',
       '% de Desconto', 'RE compra por', 'RE Vende por', 'RE lucra  (R$)',
       'MATCH', 'PDV', 'UF', 'DESCRIÇÃO PDV', 'ANALISTA'],
      dtype='object')

In [24]:
df_draft['PDV'] = df_draft['PDV'].astype(str)

In [25]:
df_draft['SKU'] = df_draft['SKU'].astype(str)


In [26]:
df_tabela['Código do Item'] = df_tabela['Código do Item'].astype('str')

In [27]:
df_final = pd.merge(left=df_draft,right=df_tabela,right_on=['Código do Item','PDV'],left_on=['SKU','PDV'],how='inner')
df_final.shape  

(1518, 69)

In [28]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], on='match',how='inner')
df_final.shape

(1518, 74)

In [29]:
#df_final = pd.merge(left=df_final,right=df_pdv[['PDV', 'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC','UF', 'MARCA', 'ANALISTA']],on = 'PDV',how='inner')
df_final.shape

(1518, 74)

In [30]:
df_final['SKU'] = df_final['SKU'].astype(str) 
df_final['PDV'] = df_final['PDV'].astype(str) 
df_final = pd.merge(left=df_final,right=df_estoque[['SKU_FINAL', 'DDV PREVISTO', 'COBERTURA ATUAL','PDV']],right_on=['PDV','SKU_FINAL'],left_on=['PDV','SKU'],how='left')
df_final.shape

(1831, 77)

In [31]:

df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype(str).str.replace('.0','',regex=False) 

df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU1', 'SKU2', 'UF','Tipo Preço', 'PC', 'PV']],right_on=['UF','SKU2'],left_on=['UF','SKU'],how='left')
df_final.shape   

(1831, 82)

In [32]:
df_bi_preco['SKU1'] = df_bi_preco['SKU1'].astype(str).str.replace('.0','',regex=False) 

df_final = pd.merge(left=df_final,right=df_bi_preco[['SKU1', 'SKU2', 'UF', 'PC', 'PV']],right_on=['UF','SKU1'],left_on=['UF','SKU'],how='left')
df_final.shape   

(1831, 86)

In [33]:
#df_bi_preco = df_bi_preco[df_bi_preco['MARCA']=='EUDORA']

In [34]:
df_final['PRECO DE COMPRA'] = np.where(~df_final['PC_x'].isna(),df_final['PC_x'],df_final['PC_y'])

df_final['PRECO DE VENDA'] = np.where(~df_final['PV_x'].isna(),df_final['PV_x'],df_final['PV_y'])



In [35]:
df_estoque = df_estoque.rename(columns={'SKU_FINAL':'SKU_PARA_VALIDACAO'})
df_final = pd.merge( left= df_final, right = df_estoque[['SKU_PARA_VALIDACAO','Arquivo_Origem']], left_on= 'SKU', right_on='SKU_PARA_VALIDACAO', how='left')

In [36]:
df_final.columns

Index(['PDV', 'Classe', 'SKU', 'Descrição', 'Categoria_x', 'Subcategoria',
       'Lançamento', 'Desativação', 'Histórico de Vendas do Ciclo 202408',
       'Histórico de Vendas do Ciclo 202409',
       'Histórico de Vendas do Ciclo 202410',
       'Histórico de Vendas do Ciclo 202411',
       'Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo Atual', 'Dias sem venda',
       'Projeção Próximo Ciclo', 'Projeção Próximo 

In [37]:
df_final = df_final.drop(columns=['Desativação','Lançamento',
'Promoção Próximo Ciclo',
'Compra inteligente semanal/Sugestão de compra',
'Planograma',
'Carteira Bloqueada Para Novos Pedidos',
'Preço Sell In',
'Quantidade',
'Item analisado',
'Promoção Próximo Ciclo + 1',
'SKU_PARA_VALIDACAO',
'Ciclo_y'
])

In [38]:
df_final['PDV_SKU'] = df_final['PDV'].astype(str) + df_final['SKU'].astype(str) 
df_final['UFPRODUTO'] = df_final['UF'].astype(str) + df_final['SKU'].astype(str)

df_final.shape

(101091, 80)

In [39]:
df_final['Projeção Próximo Ciclo + 1'].value_counts()

Projeção Próximo Ciclo + 1
0      11230
1       6095
2       5693
4       5037
3       4691
       ...  
60        13
575       13
197       13
351       13
118       13
Name: count, Length: 129, dtype: int64

In [40]:
df_final['PROJEÇÃO DO CICLO PROMOCIONADO'] =df_final['Projeção Próximo Ciclo + 1'] - df_final['Projeção Próximo Ciclo'] # projeção do ciclo em estudo

In [41]:
df_final['PROJEÇÃO DO CICLO PROMOCIONADO'].value_counts()

PROJEÇÃO DO CICLO PROMOCIONADO
0      11243
1       7913
2       7288
4       5839
5       5191
       ...  
175       13
312       13
108       13
69        13
161       13
Name: count, Length: 115, dtype: int64

In [42]:
df_final['Data Prevista Regularização'] = df_final['Data Prevista Regularização'].astype(str).replace('0','REGULAR')

In [43]:
df_final = df_final.rename(columns={'Arquivo_Origem': 'MARCA'})

In [44]:
df_final = df_final[~df_final['MARCA'].isna()]
df_final['MARCA'].isna().sum()

np.int64(0)

In [45]:
df_final = df_final.drop_duplicates()
df_final.shape

(1822, 81)

In [46]:
df_final.columns

Index(['PDV', 'Classe', 'SKU', 'Descrição', 'Categoria_x', 'Subcategoria',
       'Histórico de Vendas do Ciclo 202408',
       'Histórico de Vendas do Ciclo 202409',
       'Histórico de Vendas do Ciclo 202410',
       'Histórico de Vendas do Ciclo 202411',
       'Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo Atual', 'Dias sem venda',
       'Projeção Próximo Ciclo', 'Projeção Próximo Ciclo + 1', 'Estoque Atual',


In [47]:
# Define list of target columns
sales_2024_cols = df_final.columns[6:24]
# Create a new column with the row-wise max
df_final['PICO DE VENDAS 2024'] = df_final[sales_2024_cols].max(axis=1)



In [48]:
vendas_6_meses = df_final.columns[17:23]

df_final['Pico Vendas Ultimos 6 ciclos'] = df_final[vendas_6_meses].max(axis=1)

In [49]:
CRESCIMENTO = (df_final[df_final.columns[17]].sum() - df_final[df_final.columns[22]].sum())/df_final[df_final.columns[17]].sum() 
print(CRESCIMENTO)

df_final['CRESCIMENTO'] = .2

-0.14227416063810053


In [50]:
mesmo_ciclo_ano_passado = df_final.columns[8:9]
ciclo_ano_passado = df_final.columns[8:9].str.split(" ")[0][-1]
df_final[ciclo_ano_passado] = df_final[mesmo_ciclo_ano_passado]

In [51]:
df_final.columns[8:9].str.split(" ")[0][-1]

'202410'

In [52]:
vendas_todos_historicos = df_final.columns[17:23]

df_final['MEDIANA DO HISTÓRICO'] = df_final[vendas_todos_historicos].median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[vendas_todos_historicos].mean(axis=1)

df_final['MEDIANA DO HISTÓRICO'] = np.where(df_final['MEDIANA DO HISTÓRICO'] <1,df_final['MEDIA DO HISTÓRICO'],df_final['MEDIANA DO HISTÓRICO'])


In [53]:
CRESCIMENTO

np.float64(-0.14227416063810053)

In [54]:
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO'] * df_final[ciclo_ano_passado] + df_final[ciclo_ano_passado] < df_final['MEDIANA DO HISTÓRICO'],
                                    round(df_final['CRESCIMENTO'] * df_final['MEDIANA DO HISTÓRICO']+ df_final['MEDIANA DO HISTÓRICO'],0), 
                                    round(df_final['CRESCIMENTO']*df_final[ciclo_ano_passado]+df_final[ciclo_ano_passado],0))

In [55]:
df_final = df_final.rename(columns={df_final.columns[18]: "C-4", df_final.columns[19]: "C-3",df_final.columns[20]: "C-2",df_final.columns[21]: "C-1"})

In [56]:
df_final.drop(columns=df_final.columns[6:18], inplace=True)


In [57]:
# List all columns except the two
cols_to_group_by = df_final.columns.difference(['DDV PREVISTO', 'COBERTURA ATUAL'])

# Group and aggregate
df_final_dedup = (
    df_final
    .groupby(list(cols_to_group_by), dropna=False)[['DDV PREVISTO', 'COBERTURA ATUAL']]
    .max()
    .reset_index()
)


In [58]:
df_final['Compra inteligente Próximo Ciclo']


0         0
24        0
48        0
72        9
96        0
         ..
101026    0
101039    2
101052    1
101065    1
101078    7
Name: Compra inteligente Próximo Ciclo, Length: 1822, dtype: int64

In [59]:
df_final_dedup['DDV PREVISTO'] = df_final_dedup['DDV PREVISTO'].fillna(0.01)


In [60]:
df_final_dedup['DDV PREVISTO'] = np.where(
    df_final_dedup['DDV PREVISTO'] == 0,
    0.01,
    df_final_dedup['DDV PREVISTO']
)


In [61]:
df_final_dedup['DDV PREVISTO'].value_counts()

DDV PREVISTO
0.01     302
0.02     120
0.04     109
0.07      50
0.13      36
        ... 
1.56       1
3.58       1
3.75       1
6.98       1
10.96      1
Name: count, Length: 195, dtype: int64

In [62]:
df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = (df_final_dedup['Estoque Atual'] + df_final_dedup['Estoque em Transito']) - round(df_final_dedup['dias_ate_inicio'] * df_final_dedup['DDV PREVISTO'],0)

In [63]:
df_final_dedup['EST PROJE FINAL CICLO ATUAL'] = np.where(df_final_dedup['EST PROJE FINAL CICLO ATUAL']<0,0,df_final_dedup['EST PROJE FINAL CICLO ATUAL'])

In [64]:
df_final_dedup.columns

Index(['% de Desconto', '202410', 'ANALISTA', 'C-1', 'C-2', 'C-3', 'C-4',
       'CRESCIMENTO', 'Categoria_x', 'Categoria_y', 'Chamada Promocional',
       'Ciclo_x', 'Classe', 'Compra inteligente Próximo Ciclo',
       'Compra inteligente Próximo Ciclo + 1', 'Cód. Combo', 'Código do Item',
       'DESCRIÇÃO PDV', 'DURAÇÃO', 'Data Prevista Regularização', 'Descrição',
       'Descrição do Item', 'Dias sem venda', 'EAM', 'Estoque Atual',
       'Estoque em Transito', 'Estratégia de Promoção', 'FIM CICLO',
       'Histórico de Vendas do Ciclo 202407',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo Atual', 'INICIO CICLO', 'Item Desativado',
       'MARCA', 'MATCH', 'MEDIA DO HISTÓRICO', 'MEDIANA DO HISTÓRICO', 'PC_x',
       'PC_y', 'PDV', 'PDV_SKU', 'PICO DE VENDAS 2024', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'PROJEÇÃO DO CICLO PROMOCIONADO', 'PV GINSENG',
       'PV_x', 'PV_y', 'Pedido Pendente', 'Pico Vendas Ultimos 6 ciclos',
       'Preço Pro

In [65]:
df_final_dedup['VENDAS R$ PV GINSENG'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup['PV GINSENG']

In [66]:
df_final_dedup = df_final_dedup.rename(columns={'Ciclo_x':'Ciclo'})

In [67]:
df_final_dedup['SUGESTÃO ABTASTECIMENTO	'] = ''
df_final_dedup['VENDAS R$ ABASTECIMENTO'] = ''


In [68]:
df_final_dedup['RBV 202406'] = df_final_dedup['PRECO DE VENDA'] * df_final_dedup[ciclo_ano_passado] 

In [69]:
df_final_dedup['COB PROJETADA'] = np.where(
    df_final_dedup['DDV PREVISTO'] != 0,
    (df_final_dedup['EST PROJE FINAL CICLO ATUAL'] + df_final_dedup['PV GINSENG']) / df_final_dedup['DDV PREVISTO'],
    999)


In [70]:
df_final_dedup.drop(columns=['dias_ate_inicio','SKU_FINAL','Projeção Próximo Ciclo + 1',
                             'CRESCIMENTO'],inplace=True)

In [71]:
df_final_dedup['MARCA'] = df_final_dedup['MARCA'].str.replace('.csv','',regex=False)

In [72]:
df_final_dedup['COB PROJETADA'] = df_final_dedup['COB PROJETADA'].fillna(999)

In [73]:
df_final_dedup.columns

Index(['% de Desconto', '202410', 'ANALISTA', 'C-1', 'C-2', 'C-3', 'C-4',
       'Categoria_x', 'Categoria_y', 'Chamada Promocional', 'Ciclo', 'Classe',
       'Compra inteligente Próximo Ciclo',
       'Compra inteligente Próximo Ciclo + 1', 'Cód. Combo', 'Código do Item',
       'DESCRIÇÃO PDV', 'DURAÇÃO', 'Data Prevista Regularização', 'Descrição',
       'Descrição do Item', 'Dias sem venda', 'EAM', 'Estoque Atual',
       'Estoque em Transito', 'Estratégia de Promoção', 'FIM CICLO',
       'Histórico de Vendas do Ciclo 202407',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo Atual', 'INICIO CICLO', 'Item Desativado',
       'MARCA', 'MATCH', 'MEDIA DO HISTÓRICO', 'MEDIANA DO HISTÓRICO', 'PC_x',
       'PC_y', 'PDV', 'PDV_SKU', 'PICO DE VENDAS 2024', 'PRECO DE COMPRA',
       'PRECO DE VENDA', 'PROJEÇÃO DO CICLO PROMOCIONADO', 'PV GINSENG',
       'PV_x', 'PV_y', 'Pedido Pendente', 'Pico Vendas Ultimos 6 ciclos',
       'Preço Promocionado', 'Proj

In [74]:
marca_promo =  df_estoque['Arquivo_Origem'].iloc[0].replace('.csv','')
marca_promo

'EUD'

In [75]:
df_final.columns

Index(['PDV', 'Classe', 'SKU', 'Descrição', 'Categoria_x', 'Subcategoria',
       'C-4', 'C-3', 'C-2', 'C-1', 'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo Atual', 'Dias sem venda',
       'Projeção Próximo Ciclo', 'Projeção Próximo Ciclo + 1', 'Estoque Atual',
       'Estoque em Transito', 'Pedido Pendente',
       'Compra inteligente Próximo Ciclo',
       'Compra inteligente Próximo Ciclo + 1', 'Item Desativado',
       'Data Prevista Regularização', 'Quantidade por caixa',
       'Histórico de Vendas do Ciclo 202407', 'match', 'Ciclo_x', 'Veiculo',
       'Tipo de Promoção', 'Estratégia de Promoção', 'Tipo_mecanica',
       'Promo Período Limitado?', 'EAM', 'Categoria_y', 'Cód. Combo',
       'Código do Item', 'Descrição do Item', 'Chamada Promocional',
       'Valor do Guia', 'Preço Promocionado', '% de Desconto', 'RE compra por',
       'RE Vende por', 'RE lucra  (R$)', 'MATCH', 'UF', 'DESCRIÇÃO PDV',
       'ANALISTA', 'INICIO CICLO', 'FIM CICLO', '

In [76]:
# Passo 1: ordenar
df_sorted = df_final.sort_values(by='% de Desconto', ascending=False)

# Passo 2: obter até 3 chamadas promocionais por grupo
promo_grouped = (
    df_sorted.groupby(['SKU', 'PDV'])['Chamada Promocional']
    .apply(lambda x: x.dropna().unique()[:3])
    .apply(pd.Series)
    .rename(columns={0: 'MECÂNICA 1', 1: 'MECÂNICA 2', 2: 'MECÂNICA 3'})
    .reset_index()
)

# Passo 3: base com maior % de desconto
df_base = df_sorted.drop_duplicates(subset=['SKU', 'PDV'], keep='first').reset_index(drop=True)

# Passo 4: merge com chamadas pivotadas
df_merged = df_base.merge(promo_grouped, on=['SKU', 'PDV'], how='left')

# Corrigir dicionário: agrupar e pegar o primeiro valor válido por (SKU, PDV)
# Passo 1: dicionário com Cód. Combo único por SKU+PDV
cod_combo_map = (
    df_final
    .dropna(subset=['Cód. Combo'])
    .groupby(['SKU', 'PDV'])['Cód. Combo']
    .first()
    .to_dict()
)

# Passo 2: gerar Series com os valores mapeados
cod_combo_series = df_merged.set_index(['SKU', 'PDV']).index.map(cod_combo_map)

# Passo 3: substituir os valores diretamente
df_merged['Cód. Combo'] = cod_combo_series.where(cod_combo_series.notna(), df_merged['Cód. Combo'])



In [77]:
# Columns to bring up front
priority_cols = [
    'PDV_SKU',	'SKU',	'MARCA','INICIO CICLO',
    'FIM CICLO',	'DURAÇÃO','dias_ate_inicio',	
    'UFPRODUTO',	'Item Desativado',	'Data Prevista Regularização',
    'ANALISTA',	'UF',	'PDV',	'DESCRIÇÃO PDV',	'Classe',
    'Descrição','MECÂNICA 1',
       'MECÂNICA 2', 'MECÂNICA 3','Estoque Atual',	'COBERTURA ATUAL',
    'Estoque em Transito',	'Pedido Pendente',	'PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos',
    'C-4',	'C-3',	'C-2',	'C-1',	'Histórico de Vendas do Ciclo Atual',
    'Dias sem venda'
]

# All remaining columns
other_cols = [col for col in df_merged.columns if col not in priority_cols]

# Reorder
df_merged = df_merged[priority_cols + other_cols]


In [78]:
df_merged['INICIO CICLO'] = pd.to_datetime(df_merged['INICIO CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_merged['FIM CICLO'] = pd.to_datetime(df_merged['FIM CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

In [79]:
df_merged.columns

Index(['PDV_SKU', 'SKU', 'MARCA', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'dias_ate_inicio', 'UFPRODUTO', 'Item Desativado',
       'Data Prevista Regularização', 'ANALISTA', 'UF', 'PDV', 'DESCRIÇÃO PDV',
       'Classe', 'Descrição', 'MECÂNICA 1', 'MECÂNICA 2', 'MECÂNICA 3',
       'Estoque Atual', 'COBERTURA ATUAL', 'Estoque em Transito',
       'Pedido Pendente', 'PICO DE VENDAS 2024',
       'Pico Vendas Ultimos 6 ciclos', 'C-4', 'C-3', 'C-2', 'C-1',
       'Histórico de Vendas do Ciclo Atual', 'Dias sem venda', 'Categoria_x',
       'Subcategoria', 'Histórico de Vendas do Ciclo 202507',
       'Projeção Próximo Ciclo', 'Projeção Próximo Ciclo + 1',
       'Compra inteligente Próximo Ciclo',
       'Compra inteligente Próximo Ciclo + 1', 'Quantidade por caixa',
       'Histórico de Vendas do Ciclo 202407', 'match', 'Ciclo_x', 'Veiculo',
       'Tipo de Promoção', 'Estratégia de Promoção', 'Tipo_mecanica',
       'Promo Período Limitado?', 'EAM', 'Categoria_y', 'Cód. Combo',


In [80]:
df_merged = df_merged.loc[:, ~df_merged.columns.str.endswith('_y')]


In [81]:
df_merged.columns = df_merged.columns.str.replace('_x$', '', regex=True)


In [82]:
df_merged = df_merged.drop(columns=['Veiculo',	'Tipo de Promoção',	'Estratégia de Promoção','Tipo_mecanica'
                                    ,'Chamada Promocional','MATCH','match', 'SKU_FINAL','Descrição do Item','CRESCIMENTO',
                                    'Cód. Combo'])

In [83]:
df_merged['SUGESTÃO ANALISTA'] = ""

df_merged['SUGESTÃO COMERCIAL'] = ""

In [84]:

from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font


# Export to Excel
output_file = f'C:\\Users\\joao.herculano\\Documents\\promoção_{marca_promo}_{ciclo_mais2}_04.06.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_merged.to_excel(writer, index=False, sheet_name='Sheet1')

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='ADD8E6', end_color='ADD8E6', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)


coisas q saem

Lançamento
Subcategoria
Projeção Próximo Ciclo 
Promoção Próximo Ciclo
Compra inteligente semanal/Sugestão de compra
Compra inteligente Próximo Ciclo
Planograma
Carteira Bloqueada Para Novos Pedidos
Quantidade por caixa
Preço Sell In
Quantidade
Item analisado
Tipo Preço

>>>>>>>>>>>>>NAO ESTÁ PEGANDO O MERGE COM O DF_ESTOQUE


CRIAR PROJEÇÃO DE VENDA DO CICLO ATUAL
Compra inteligente Próximo Ciclo + 1 >>>>>>> RENAME PRA NOROMAL